# Benchmarks

In [1]:
# the notebook imports
import matplotlib.pyplot as plt
import numpy as np
# this is the convenience function
from autokoopman import auto_koopman
# for a complete example, let's create an example dataset using an included benchmark system
from autokoopman.benchmark import bio2, fhn, lalo20, prde20, robe21, spring, pendulum
from glop import Glop
import random
import copy

from sklearn.metrics import mean_squared_error, mean_absolute_percentage_error
import statistics
import os
import csv
import time

In [2]:
benches = [bio2.Bio2(), fhn.FitzHughNagumo(), lalo20.LaubLoomis(), pendulum.PendulumWithInput(beta=0.05), prde20.ProdDestr(), robe21.RobBench(), spring.Spring()]

In [3]:
def get_training_data(bench, param_dict):
    init_states = get_init_states(bench, param_dict["train_size"])
    if bench._input_vars:
        params = np.random.rand(param_dict["train_size"], 3) * 2 - 1
        steps = [make_input_step(*p, bench.teval) for p in params]
        training_data = bench.solve_ivps(initial_states=init_states, inputs=steps, teval=bench.teval)
    else:
        training_data = bench.solve_ivps(initial_states=init_states,tspan=[0.0, 10.0], 
                                         sampling_period=param_dict["samp_period"])
        
    return training_data

In [4]:
def get_init_states(bench, size, init_seed=0):
    if hasattr(bench, 'init_constrs'):
        init_states = []
        for i in range(size):
            init_state_dict = glop_init_states(bench, i+init_seed)
            init_state = []
            for name in bench.names:
                init_state.append(init_state_dict[name])
            init_states.append(init_state)
        init_states = np.array(init_states)  
    else:
        init_states = np.random.uniform(low=bench.init_set_low, 
                    high=bench.init_set_high, size=(size, len(bench.names)))
        
    return init_states

In [5]:
def glop_init_states(bench, seed):    
    constrs = []
    for constr in bench.init_constrs:
        constrs.append(constr)
    for i, (name, init_low, init_high) in enumerate(zip(bench.names, bench.init_set_low, bench.init_set_high)):
        low_constr = f"{name} >= {init_low}"
        high_constr = f"{name} <= {init_high}"
        constrs.extend([low_constr, high_constr])
        
    glop = Glop(bench.names, constrs)
    pop_item = random.randrange(len(bench.names))
    names, init_set_low, init_set_high = copy.deepcopy(bench.names), copy.deepcopy(bench.init_set_low), copy.deepcopy(bench.init_set_high)
    names.pop(pop_item)
    init_set_low.pop(pop_item)
    init_set_high.pop(pop_item)
    for i, (name, init_low, init_high) in enumerate(zip(names, init_set_low, init_set_high)):
        glop.add_tend_value_obj_fn(name, [init_low, init_high], seed+i)
    
    glop.minimize()

    sol_dict = glop.get_all_sols()    
    return sol_dict

In [6]:
def get_trajectories(bench, iv, samp_period):
    # get the model from the experiment results
    model = experiment_results['tuned_model']

    if bench._input_vars:
        test_inp = np.sin(np.linspace(0, 10, 200))

        # simulate using the learned model
        trajectory = model.solve_ivp(
            initial_state=iv,
            inputs=test_inp,
            teval=bench.teval,
        )
        # simulate the ground truth for comparison
        true_trajectory = bench.solve_ivp(
            initial_state=iv,
            inputs=test_inp,
            teval=bench.teval,
        )
        
    else:
        # simulate using the learned model
        trajectory = model.solve_ivp(
            initial_state=iv,
            tspan=(0.0, 10.0),
            sampling_period=samp_period
        )
        # simulate the ground truth for comparison
        true_trajectory = bench.solve_ivp(
            initial_state=iv,
            tspan=(0.0, 10.0),
            sampling_period=samp_period
        )
    
    return trajectory, true_trajectory

In [7]:
def test_trajectories(bench, num_tests, samp_period):
    mses = []
    perc_errors = []
    for j in range(num_tests):
        iv = get_init_states(bench, 1, j+10000)[0]
        trajectory, true_trajectory = get_trajectories(bench, iv, samp_period)
        mse = mean_squared_error(trajectory.states.T, true_trajectory.states.T)
        mses.append(mse)
        perc_error = mean_absolute_percentage_error(trajectory.states.T, true_trajectory.states.T)
        perc_errors.append(perc_error)
            
    return mses, perc_errors

In [8]:
def make_input_step(duty, on_amplitude, off_amplitude, teval):
    """produce a step response input signal for the pendulum"""
    length = len(teval)
    inp = np.zeros((length,))
    phase_idx = int(length * duty)
    inp[:phase_idx] = on_amplitude
    inp[phase_idx:] = off_amplitude
    return inp

In [9]:
def store_data(*args):
    with open('data/benches', 'a') as f:
        writer = csv.writer(f)
        writer.writerow(args)
              

In [10]:
def store_data_heads(*args):
    if not os.path.exists('data'):
        os.makedirs('data')
    
    with open('data/benches', 'w') as f:
        writer = csv.writer(f)
        writer.writerow(args)

In [11]:
def plot(trajectory, true_trajectory):
    plt.figure(figsize=(10, 6))
    # plot the results
    #plt.plot(true_trajectory.states[:, 5])
    plt.plot(trajectory.states.T[0], trajectory.states.T[1],label='Trajectory Prediction')
    plt.plot(true_trajectory.states.T[0], true_trajectory.states.T[1],label='Ground Truth')

    plt.xlabel("$x_1$")
    plt.ylabel("$x_2$")
    plt.grid()
    plt.legend()
    plt.title("Bio2 Test Trajectory Plot")
    plt.show()

In [12]:
def plot_trajectory(bench, seed=100):
    iv = get_init_states(bench, 1, seed)[0]
    trajectory, true_trajectory = get_trajectories(bench, iv, param_dict["samp_period"])
    plot(trajectory, true_trajectory)

In [ ]:
store_data_heads("time(s)", "mean", "perc_error")
for bench in benches:
    np.random.seed(0)
    param_dict = {"train_size":10,"samp_period":0.1,"obs_type":"deep","opt":"grid","n_obs":200,
                  "grid_param_slices":5,"n_splits":5,"rank":(1, 200, 40)}
    # generate training data
    training_data = get_training_data(bench, param_dict)
    start = time.time()
    # learn model from data
    experiment_results = auto_koopman(
        training_data,          # list of trajectories
        sampling_period=param_dict["samp_period"],    # sampling period of trajectory snapshots
        obs_type=param_dict["obs_type"],         # use Random Fourier Features Observables
        opt=param_dict["opt"],             # grid search to find best hyperparameters
        n_obs=param_dict["n_obs"],              # maximum number of observables to try
        max_opt_iter=200,       # maximum number of optimization iterations
        grid_param_slices=param_dict["grid_param_slices"],# for grid search, number of slices for each parameter
        n_splits=param_dict["n_splits"],             # k-folds validation for tuning, helps stabilize the scoring
        rank=param_dict["rank"]       # rank range (start, stop, step) DMD hyperparameter
    )
    end = time.time()

    mses = [-1]
    perc_errors = [-1]
    try:
        mses, perc_errors = test_trajectories(bench, 10, param_dict["samp_period"])
    except ValueError:
        print("can't compute for this setting")
       
    time_taken = round(end - start, 3)
    print("time taken: ", time_taken)
    print("The average mean square error is ", statistics.mean(mses))

    store_data(time_taken, statistics.mean(mses), statistics.mean(perc_errors))

100%|████████████████████████████████████████| 500/500 [00:03<00:00, 155.85it/s]

100%|████████████████████████████████████████| 500/500 [00:03<00:00, 164.49it/s]

100%|████████████████████████████████████████| 500/500 [00:03<00:00, 162.24it/s]

 13%|█████▍                                   | 67/500 [00:00<00:02, 160.44it/s]


100%|████████████████████████████████████████| 500/500 [00:03<00:00, 163.87it/s]

 72%|█████████████████████████████▌           | 360/500 [00:04<00:01, 85.46it/s]


100%|█████████████████████████████████████████| 500/500 [00:05<00:00, 85.52it/s]

100%|█████████████████████████████████████████| 500/500 [00:05<00:00, 86.61it/s]

 45%|██████████████████▍                      | 225/500 [00:02<00:03, 84.76it/s]


100%|█████████████████████████████████████████| 500/500 [00:05<00:00, 85.55it/s]

100%|█████████████████████████████████████████| 500/500 [00:05<00:00, 86.40it/s]

 18%|███████▌                                  | 90/500 [00:01<00:04, 85.59it/s]


 60%|████████████████████████▌                | 300/500 [00:05<00:03, 57.90it/s]


...

100%|█████████████████████████████████████████| 500/500 [00:11<00:00, 42.09it/s]

 40%|████████████████▍                        | 200/500 [00:04<00:07, 42.26it/s]


100%|█████████████████████████████████████████| 500/500 [00:11<00:00, 42.17it/s]

 36%|██████████████▊                          | 180/500 [00:04<00:07, 42.32it/s]


100%|█████████████████████████████████████████| 500/500 [00:11<00:00, 42.20it/s]

 32%|█████████████                            | 160/500 [00:03<00:08, 42.31it/s]


100%|█████████████████████████████████████████| 500/500 [00:11<00:00, 42.09it/s]

 28%|███████████▍                             | 140/500 [00:03<00:08, 42.10it/s]


 61%|█████████████████████████                | 305/500 [00:07<00:04, 42.06it/s]